# Color indicates the upper bound estimation of total population

In [14]:
import folium
from folium import plugins
import psycopg2
import json
import branca.colormap as cm
import math

# ----------------------------
# Connect to PostGIS
# ----------------------------
conn = psycopg2.connect(
    dbname="utahdaminundationprofiles_aug9_2025",
    user="admin",
    password="admin",
    host="localhost",
    port=5432
)
cur = conn.cursor()

# ----------------------------
# Create folium map
# ----------------------------
m = folium.Map(location=[40.7607, -111.8939], zoom_start=7)

# ----------------------------
# Query top 50 largest dams (including 0-intersection)
# ----------------------------
cur.execute("""
WITH census_geoms AS (
    SELECT
        objectid,
        pop,
        geom
    FROM
        utah_census_tracts_svi
),
dams_with_counts AS (
    SELECT
        d.objectid,
        d.damnumber,
        d.name,
        d.shape_area,
        ST_AsGeoJSON(d.geom) AS geojson,
        SUM(c.pop) AS upper_total_pop,
        SUM(c.pop * ST_Area(ST_Transform(ST_Intersection(d.geom, c.geom), 26912)) / ST_Area(ST_Transform(c.geom, 26912))) AS est_total_pop
    FROM
        utah_dam_inundation_zones d
    LEFT JOIN
        census_geoms c ON ST_Intersects(d.geom, c.geom)
    GROUP BY
        d.objectid, d.damnumber, d.name, d.shape_area, d.geom
)
    SELECT *
    FROM dams_with_counts
    ORDER BY shape_area DESC
    LIMIT 50;
""")

results = cur.fetchall()

total_pop = [row[5] for row in results if row[5] is not None]
min_total_pop = min(total_pop)
max_total_pop = max(total_pop)

# ----------------------------
# Define colormap
# ----------------------------
colormap = cm.linear.Reds_09.scale(min_total_pop, max_total_pop)

colormap.caption = "Total Population Affected per Dam (Upper Bound Estimation)"
colormap.add_to(m)






# ----------------------------
# Add each dam to map
# ----------------------------
for dam_id, dam_num, name, area_m2, geom_json, upper_total_pop, est_total_pop in results:
    geojson = json.loads(geom_json)
    area_km2 = float(area_m2) / 1_000_000 if area_m2 else 0.0
    upper_total_pop = int(upper_total_pop) if upper_total_pop else 0.0
    est_total_pop = math.ceil(est_total_pop) if est_total_pop else 0.0
    popup_html = f"""
        <b>Dam:</b> {name or 'Unknown'}<br>
        <b>Dam Number:</b> {dam_num or 'Unknown'}<br>
        <b>Inundation Area:</b> {area_km2:.2f} km²<br>
        <b>Total Population Affected (Upper Bound):</b> {upper_total_pop} <br>
        <b>Total Population Affected (Area-Proportional Estimate):</b> {est_total_pop} <br>
    """

    folium.GeoJson(
        data=geojson,
        style_function=lambda feature, var=upper_total_pop: {
            "fillColor": colormap(var),
            "color": "black",
            "weight": 1,
            "fillOpacity": 0.6
        },
        highlight_function=lambda x: {"weight": 2, "color": "yellow"},
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=name
    ).add_to(m)



# ----------------------------
# Cleanup
# ----------------------------
cur.close()
conn.close()


# ----------------------------
# Add fullscreen button and save
# ----------------------------
plugins.Fullscreen().add_to(m)
m.save("./html/census_dams_colored_by_population.html")
m

# Color indicates the area-proportional estimation of total population

In [15]:
import folium
from folium import plugins
import psycopg2
import json
import branca.colormap as cm
import math

# ----------------------------
# Connect to PostGIS
# ----------------------------
conn = psycopg2.connect(
    dbname="utahdaminundationprofiles_aug9_2025",
    user="admin",
    password="admin",
    host="localhost",
    port=5432
)
cur = conn.cursor()

# ----------------------------
# Create folium map
# ----------------------------
m = folium.Map(location=[40.7607, -111.8939], zoom_start=7)

# ----------------------------
# Query top 50 largest dams (including 0-intersection)
# ----------------------------
cur.execute("""
WITH census_geoms AS (
    SELECT
        objectid,
        pop,
        geom
    FROM
        utah_census_tracts_svi
),
dams_with_counts AS (
    SELECT
        d.objectid,
        d.damnumber,
        d.name,
        d.shape_area,
        ST_AsGeoJSON(d.geom) AS geojson,
        SUM(c.pop) AS upper_total_pop,
        SUM(c.pop * ST_Area(ST_Transform(ST_Intersection(d.geom, c.geom), 26912)) / ST_Area(ST_Transform(c.geom, 26912))) AS est_total_pop
    FROM
        utah_dam_inundation_zones d
    LEFT JOIN
        census_geoms c ON ST_Intersects(d.geom, c.geom)
    GROUP BY
        d.objectid, d.damnumber, d.name, d.shape_area, d.geom
)
    SELECT *
    FROM dams_with_counts
    ORDER BY shape_area DESC
    LIMIT 50;
""")

results = cur.fetchall()

total_pop = [row[6] for row in results if row[6] is not None]
min_total_pop = math.ceil(min(total_pop)
max_total_pop = math.ceil(max(total_pop))

# ----------------------------
# Define colormap
# ----------------------------
colormap = cm.linear.Reds_09.scale(min_total_pop, max_total_pop)

colormap.caption = "Total Population Affected per Dam (Area-proportional Estimation)"
colormap.add_to(m)






# ----------------------------
# Add each dam to map
# ----------------------------
for dam_id, dam_num, name, area_m2, geom_json, upper_total_pop, est_total_pop in results:
    geojson = json.loads(geom_json)
    area_km2 = float(area_m2) / 1_000_000 if area_m2 else 0.0
    upper_total_pop = int(upper_total_pop) if upper_total_pop else 0.0
    est_total_pop = math.ceil(est_total_pop) if est_total_pop else 0.0
    popup_html = f"""
        <b>Dam:</b> {name or 'Unknown'}<br>
        <b>Dam Number:</b> {dam_num or 'Unknown'}<br>
        <b>Inundation Area:</b> {area_km2:.2f} km²<br>
        <b>Total Population Affected (Upper Bound):</b> {upper_total_pop} <br>
        <b>Total Population Affected (Area-Proportional Estimate):</b> {est_total_pop} <br>
    """

    folium.GeoJson(
        data=geojson,
        style_function=lambda feature, var=est_total_pop: {
            "fillColor": colormap(var),
            "color": "black",
            "weight": 1,
            "fillOpacity": 0.6
        },
        highlight_function=lambda x: {"weight": 2, "color": "yellow"},
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=name
    ).add_to(m)



# ----------------------------
# Cleanup
# ----------------------------
cur.close()
conn.close()


# ----------------------------
# Add fullscreen button and save
# ----------------------------
plugins.Fullscreen().add_to(m)
m.save("./html/census_dams_colored_by_area_proportional_population.html")
m